# Tarea 1: Redes Densas

In [1]:
# Librerias
import numpy as np
import cupy as cp
import pandas as pd

### Ejercicio 1 - Red de unidades de umbral lineal para aproximar la operación XNOR con función de activación escalón unitario


![data](../figs/puerta-logica-xnor.png)

In [2]:
def esc_un(z):
    for ind, el in enumerate(z):
        if el > 0:
            z[ind] = 1
        else:
            z[ind] = 0
        return z


def entropia_cruzada_binaria(y, p):
    p[p == 0] = np.nextafter(0., 1.)
    p[p == 1] = np.nextafter(1., 0.)
    return -(np.log(p[y == 1]).sum() + np.log(1 - p[y == 0]).sum())

def exactitud(y, y_predicha):
    return (y == y_predicha).mean() * 100

def hacia_adelante(x, W1, b1, W2, b2):
    z2 = np.dot(W1.T, x[:, np.newaxis]) + b1
    a2 = esc_un(z2)
    z3 = np.dot(W2.T, a2) + b2
    y_hat = esc_un(z3)
  
    return z2, a2, z3, y_hat

def retropropagacion(X, y, alpha = 0.01, n_epocas = 100, n_ocultas = 10):
    n_ejemplos = X.shape[0]
    n_entradas = X.shape[1]
    
    # Inicialización de las matrices de pesos W y b
    W1 = np.sqrt(1.0 / n_entradas) * np.random.randn(n_entradas, n_ocultas)
    b1 = np.zeros((n_ocultas, 1))
    
    W2 = np.sqrt(1.0 / n_ocultas) * np.random.randn(n_ocultas, 1)
    b2 = np.zeros((1, 1))
    
    perdidas = np.zeros((n_epocas))
    exactitudes = np.zeros((n_epocas))
    y_predicha = np.zeros((y.shape))
    for i in range(n_epocas):
        for j in range(n_ejemplos):
            z2, a2, z3, y_hat = hacia_adelante(X[j], W1, b1, W2, b2)

            # cálculo de gradiente para W2 por retropropagación
            d1 = (y_hat - y[j])/(y_hat*(1-y_hat))
            W2 = W2 - alpha * np.outer(a2, d1)
            b2 = b2 - alpha * (y_hat - y[j])
#             d1 = y_hat - y[j]
#             error  = y[j] - y_hat
#             W2 = W2 + np.outer(a2, error * d1)
#             b2 = b2 + error

            # cálculo de gradiente para W1 por retropropagación
    
            d2 = np.dot(W2, d1) 
            W1 = W1 - alpha * np.outer(X[j], d2)
            b1 = b1 - alpha * d2
#             d2 = W2.dot(d1)
#             W1 =  W1 + np.outer(X[j],  error * d2)
#             b1 = b1 + error

            y_predicha[j] = y_hat
            
        # calcula la pérdida en la época
        perdidas[i] = entropia_cruzada_binaria(y, y_predicha)
        exactitudes[i] = exactitud(y, np.round(y_predicha))
        print('Epoch {0}: Pérdida = {1} Exactitud = {2}'.format(i, 
                                                              perdidas[i], 
                                                              exactitudes[i]))

    return W1, W2, perdidas, exactitudes

# ejemplo (XOR)
X = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
y = np.array([[1, 0, 0, 1]]).T

np.random.seed(0)
W1, W2, perdidas, exactitudes = retropropagacion(X, 
                                                 y, 
                                                 alpha = 1.0, 
                                                 n_epocas = 100,
                                                 n_ocultas = 10000)

C:\Users\mario\Anaconda3\envs\cap\lib\site-packages\ipykernel_launcher.py:45: RuntimeWarning: divide by zero encountered in true_divide
C:\Users\mario\Anaconda3\envs\cap\lib\site-packages\numpy\core\numeric.py:909: RuntimeWarning: invalid value encountered in multiply
  return multiply(a.ravel()[:, newaxis], b.ravel()[newaxis, :], out)
C:\Users\mario\Anaconda3\envs\cap\lib\site-packages\ipykernel_launcher.py:45: RuntimeWarning: invalid value encountered in true_divide


Epoch 0: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 1: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 2: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 3: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 4: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 5: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 6: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 7: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 8: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 9: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 10: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 11: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 12: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 13: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 14: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 15: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 16: Pérdida = 1488.8801438427624 Exactitud = 50.0
Epoch 17: Pérdida = 1488.8801438427624 Exactitud = 50.0
Ep

In [3]:
def sigmoide(z):
    return 1 / (1 + np.exp(-z))
def derivada_sigmoide(x):
    return np.multiply(sigmoide(x), (1.0 - sigmoide(x)))
def entropia_cruzada_binaria(y, p):
    p[p == 0] = np.nextafter(0., 1.)
    p[p == 1] = np.nextafter(1., 0.)
    return -(np.log(p[y == 1]).sum() + np.log(1 - p[y == 0]).sum())
def exactitud(y, y_predicha):
    return (y == y_predicha).mean() * 100
def hacia_adelante(x, W1, b1, W2, b2):
    z2 = np.dot(W1.T, x[:, np.newaxis]) + b1
    a2 = sigmoide(z2)
    z3 = np.dot(W2.T, a2) + b2
    y_hat = sigmoide(z3)
    
    return z2, a2, z3, y_hat
# def hacia_adelante(x, W1, b1, W2, b2):
#     z2 = np.dot(W1.T, x[:, np.newaxis]) + b1
#     a2, cache_relu = relu(z2)
#     z3 = np.dot(W2.T, a2) + b2
#     y_hat = sigmoide(z3)
  
#     return cache_relu, z2, a2, z3, y_hat

def retropropagacion(X, y, alpha = 0.01, n_epocas = 100, n_ocultas = 10):
    n_ejemplos = X.shape[0]
    n_entradas = X.shape[1]
    
    # Inicialización de las matrices de pesos W y b
    W1 = np.sqrt(1.0 / n_entradas) * np.random.randn(n_entradas, n_ocultas)
    b1 = np.zeros((n_ocultas, 1))
    
    W2 = np.sqrt(1.0 / n_ocultas) * np.random.randn(n_ocultas, 1)
    b2 = np.zeros((1, 1))
    
    perdidas = np.zeros((n_epocas))
    exactitudes = np.zeros((n_epocas))
    y_predicha = np.zeros((y.shape))
    for i in range(n_epocas):
        for j in range(n_ejemplos):
            z2, a2, z3, y_hat = hacia_adelante(X[j], W1, b1, W2, b2)
#             cache_relu,z2, a2, z3, y_hat = hacia_adelante(X[j], W1, b1, W2, b2)

            # cálculo de gradiente para W2 por retropropagación
            delta3 = (y_hat - y[j]) * derivada_sigmoide(z3)
#             W2 = W2 - alpha * np.outer(a2, delta3)
#             b2 = b2 - alpha * delta3

            # cálculo de gradiente para W1 por retropropagación
#             dacum = np.dot(W2, delta3)
#             delta2 = np.dot(W2, delta3) * derivada_relu(dacum, cache_relu)
            delta2 = np.dot(W2, delta3) * derivada_sigmoide(z2)
    
            W2 = W2 - alpha * np.outer(a2, delta3)
            b2 = b2 - alpha * delta3
            W1 = W1 - alpha * np.outer(X[j], delta2)
            b1 = b1 - alpha * delta2

            y_predicha[j] = y_hat
            
        # calcula la pérdida en la época
        perdidas[i] = entropia_cruzada_binaria(y, y_predicha)
        exactitudes[i] = exactitud(y, np.round(y_predicha))
        print('Epoch {0}: Pérdida = {1} Exactitud = {2}'.format(i, 
                                                              perdidas[i], 
                                                              exactitudes[i]))

    return W1, W2, perdidas, exactitudes

X = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
y = np.array([[1, 0, 0, 1]]).T

np.random.seed(0)
W1, W2, perdidas, exactitudes = retropropagacion(X, 
                                                 y, 
                                                 alpha = 1.0, 
                                                 n_epocas = 300,
                                                 n_ocultas = 10)

Epoch 0: Pérdida = 3.5059110428411926 Exactitud = 25.0
Epoch 1: Pérdida = 3.4878876011111695 Exactitud = 25.0
Epoch 2: Pérdida = 3.4785772066522553 Exactitud = 50.0
Epoch 3: Pérdida = 3.4724932016875263 Exactitud = 50.0
Epoch 4: Pérdida = 3.4677243323661067 Exactitud = 50.0
Epoch 5: Pérdida = 3.46355149777041 Exactitud = 50.0
Epoch 6: Pérdida = 3.4596805413459606 Exactitud = 50.0
Epoch 7: Pérdida = 3.45598264651006 Exactitud = 50.0
Epoch 8: Pérdida = 3.4523985278159457 Exactitud = 50.0
Epoch 9: Pérdida = 3.448899797438961 Exactitud = 50.0
Epoch 10: Pérdida = 3.445472274707056 Exactitud = 50.0
Epoch 11: Pérdida = 3.442108442954913 Exactitud = 50.0
Epoch 12: Pérdida = 3.438803948891633 Exactitud = 25.0
Epoch 13: Pérdida = 3.435555953748206 Exactitud = 25.0
Epoch 14: Pérdida = 3.4323623500706493 Exactitud = 25.0
Epoch 15: Pérdida = 3.42922138770387 Exactitud = 25.0
Epoch 16: Pérdida = 3.426131494448761 Exactitud = 25.0
Epoch 17: Pérdida = 3.4230911897690848 Exactitud = 25.0
Epoch 18: Pérd

In [4]:
# En esta implementación se puede observar que que utilizando una arquitectura de una sola capa oculta
# con dos neuronas una que represente una compuerta OR y una NAND, y en la capa de salida con una sola
# neurona que tambien represente una compuerta NAND es posible aproximar de buena manera una XNOR.

def escalon(z):
    if z > 0.0:
        return 1.0
    else:
        return 0.0
    
def multicapa(x, W1, b1, W2, b2):
    escv = np.vectorize(escalon)
    a = escv(np.dot(W1.T, x) + b1)
    return escv(np.dot(W2.T, a) + b2)

X = np.array([[0., 0.], [0., 1.], [1., 0.], [1., 1.]])
y_xor = np.array([0., 1., 1., 0.])

W1 = np.array([[10, -10], [10, -10]])
b1 = np.array([-5, 15])

W2 = np.array([[-10], [-10]])
b2 = np.array([15])

print('W_1 = [{0}{1}], b_1 = {2}'.format(W1[0, :], W1[1, :], b1))
print('W_2 = [{0}{1}], b_2 = {2}'.format(W2[0], W2[1], b2))
print('-----------------------------')
print('x_1 \tx_2 \ty\ty_hat')
print('-----------------------------')
for i in range(X.shape[0]):
    y_hat = multicapa(X[i], W1, b1, W2, b2)
    print('{0}\t{1}\t{2}\t{3}'.format(X[i, 0], X[i, 1], y_xor[i], y_hat[0]))

W_1 = [[ 10 -10][ 10 -10]], b_1 = [-5 15]
W_2 = [[-10][-10]], b_2 = [15]
-----------------------------
x_1 	x_2 	y	y_hat
-----------------------------
0.0	0.0	0.0	1.0
0.0	1.0	1.0	0.0
1.0	0.0	1.0	0.0
1.0	1.0	0.0	1.0


### Ejercicio 2 - Retropropagación en Red Densa

In [5]:
#Primero se contruyen las funciones que serviran  para poder entrenar una arquitectura de dos capas ocultas con una 
#opcion seleccionable de funcion de activación en las capas internas, con la función de pérdida de entropia cruzada binaria
# proporcionando en cada epoca la perdida obtenida y la exactitud obtenida

#Realizamos el proceso de activación relu hacia adelante 
def relu(x):
    out = np.zeros_like(x)
    for idx,i in enumerate(x):
        out[idx] = np.maximum(0,i)
    cache = x
    return out, cache

#Realizamos el proceso de activación relu hacia atras en la retropropagación, 
#el gradiente que entra se distribuye al valor mayor.
def derivada_relu(dout, cache):
    x =  cache
    drelu = np.zeros_like(x)
    for idx,i in enumerate(x):
        if i > 0:
            val = dout[idx]
        else:
            val = 0
        drelu[idx] = val
    return drelu
#Realizamos el proceso de activación sigmoide hacia adelante para obtener la probabilidad y saber que predicción dar. 
def sigmoide(z):
    return 1 / (1 + np.exp(-z))
#Con la derivada de la función sigmoide se calcula  el paso del gradiente por esta funcón deactivación
def derivada_sigmoide(x):
    return np.multiply(sigmoide(x), (1.0 - sigmoide(x)))
# Entropía cruzada binaria para obtener la perdida y poder retropropagar.
def entropia_cruzada_binaria(y, p):
    p[p == 0] = np.nextafter(0., 1.)
    p[p == 1] = np.nextafter(1., 0.)
    return -(np.log(p[y == 1]).sum() + np.log(1 - p[y == 0]).sum())
# Se obtiene la exactitud: prediciones_correctas/total_examples.
def exactitud(y, y_predicha):
    return (y == y_predicha).mean() * 100
#Realizamos el procesos de la suma pesada mas el bias, para cualquier capa. 
def paso_delante(x, w, b):
    logits = 0
    sums = x.T.dot(w)
    logits = sums + np.squeeze(b)
    cache = (x, w, b)
    return logits, cache

In [6]:
# Se define una función para realizar el entrenamiento donde se puede seleccionar:
#    - El numero de epocas a entrenar
#    - La taza de aprendizaje
#    - Las dimensiones de ambas capas ocultas.
#    - La variación que tengan los pesos estando centrado el conjunto en cero
#    - La función de activación de activación usada en las capas internas, entre relu y sigmoide
# Obligatoriamente se le tiene que proveer a la función los ejemplos es decir la info de entrenameinto y las etiquetas.

def retroprop(X, y, alpha = 0.01, n_epocas = 100, dim_ocultas = [10,10], varianza_pesos = 1e-2, actv_int = 'sigmoide'):
    # se obtiene información de la información de entrada para la creación de pesos y las iteraciónes
    n_ejemplos = X.shape[0]
    n_entradas = X.shape[1]
    
    # Inicialización de las matrices de pesos W y b, 
    #Centados en 0 donde tendremos una variación de los mismos elegida por el usiario
    W1 = np.random.normal(0, varianza_pesos, [n_entradas,dim_ocultas[0]])
    b1 = np.zeros((dim_ocultas[0],1))
    
    W2 = np.random.normal(0, varianza_pesos, [dim_ocultas[0],dim_ocultas[1]])
    b2 = np.zeros((dim_ocultas[1],1))
    
    W3 = np.random.normal(0,varianza_pesos, [dim_ocultas[1],1])
    b3 = np.zeros((1,1))

    perdidas = np.zeros((n_epocas))
    exactitudes = np.zeros((n_epocas))
    y_predicha = np.zeros((y.shape))
    for i in range(n_epocas):
        for j in range(n_ejemplos):
            
            # Para capas internas con función de activación relu 
            if actv_int == 'relu':
                # realizamos el paso hacia adelante para obtener la probabilidad en predicción
                z1, c_z1 = paso_delante(X[j], W1, b1)
                a1, c_relu1 = relu(z1)
                z2, c_z2 = paso_delante(a1, W2, b2)
                a2, c_relu2 = relu(z2)
                z3, c_z3 = paso_delante(a2, W3, b3)
                y_hat = sigmoide(z3)

                # cálculo de gradiente para W3 por retropropagación
                dEBC = (y_hat - y[j])/(y_hat*(1-y_hat)) #* derivada_sigmoide(z3)
                delta3 = dEBC * derivada_sigmoide(z3)
    #            delta3 = (y_hat - y[j]) * derivada_sigmoide(z3)
                W3 = W3 - alpha * a2[..., np.newaxis].dot(delta3[..., np.newaxis].T)
                b3 = b3 - alpha * delta3[..., np.newaxis]

                # cálculo de gradiente para W2 por retropropagación
                dacum2 = np.dot(W3, delta3)
                delta2 = np.dot(W3, delta3) * derivada_relu(dacum2, c_relu2)
                W2 = W2 - alpha * a1[..., np.newaxis].dot(delta2[..., np.newaxis].T)
                b2 = b2- alpha * delta2[..., np.newaxis]

                # cálculo de gradiente para W1 por retropropagación
                dacum1 = np.dot(W2, delta2)
                delta1 = np.dot(W2, delta2) * derivada_relu(dacum1, c_relu1)
                W1 = W1 - alpha * X[j][..., np.newaxis].dot(delta1[..., np.newaxis].T)
                b1 = b1 - alpha * delta1[..., np.newaxis]
            
            #para capas internas con función de activación sigmoide
            elif actv_int == 'sigmoide':
                # realizamos el paso hacia adelante para obtener la probabilidad en predicción
                z1, c_z1 = paso_delante(X[j], W1, b1)
                a1 = sigmoide(z1)
                z2, c_z2 = paso_delante(a1, W2, b2)
                a2 = sigmoide(z2)
                z3, c_z3 = paso_delante(a2, W3, b3)
                y_hat = sigmoide(z3)

                # cálculo de gradiente para W3 por retropropagación
                dEBC = (y_hat - y[j])/(y_hat*(1-y_hat)) #* derivada_sigmoide(z3)
                delta3 = dEBC * derivada_sigmoide(z3)
                #delta3 = (y_hat - y[j]) * derivada_sigmoide(z3)
                W3 = W3 - alpha * a2[..., np.newaxis].dot(delta3[..., np.newaxis])
                b3 = b3 - alpha * delta3[..., np.newaxis]

                # cálculo de gradiente para W2 por retropropagación
                delta2 = np.dot(W3, delta3) * derivada_sigmoide(z2)
                W2 = W2 - alpha * a1[..., np.newaxis].dot(delta2[..., np.newaxis].T)
                b2 = b2- alpha * delta2[..., np.newaxis]

                # cálculo de gradiente para W1 por retropropagación
                delta1 = np.dot(W2, delta2) * derivada_sigmoide(z1)
                W1 = W1 - alpha * X[j][..., np.newaxis].dot(delta1[..., np.newaxis].T)
                b1 = b1 - alpha * delta1[..., np.newaxis]
            # Por si no se tiene una función de activación valida. 
            else: 
                raise Exception("No se cuenta con esa función de activación, es una palabra erronea o un typo")
            # se almacenan las predicciones
            y_predicha[j] = y_hat
        
        # calcula la pérdida y la exactitud en la época 
        perdidas[i] = entropia_cruzada_binaria(y, y_predicha)
        exactitudes[i] = exactitud(y, np.round(y_predicha))
        print('Epoch {0}: Pérdida = {1} Exactitud = {2}'.format(i, 
                                                              perdidas[i], 
                                                              exactitudes[i]))

    return W1, W2, perdidas, exactitudes

#### Convergencia rápida con activación interna sigmoide

In [34]:
#Preparamos la información, y las etiquetas
X = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
y = np.array([[1, 0, 0, 1]]).T
#np.random.seed(0)
# Tasa de aprendizaje, dimensiones internas y variación de pesos efectivos para función de activación sigmoide
W1, W2, perdidas, exactitudes = retroprop(X, y, alpha = 1, n_epocas = 300, dim_ocultas = [10,10], varianza_pesos = 5, actv_int = 'sigmoide')

Epoch 0: Pérdida = 13.655067603370396 Exactitud = 50.0
Epoch 1: Pérdida = 9.665316103718643 Exactitud = 0.0
Epoch 2: Pérdida = 6.837433029961698 Exactitud = 50.0
Epoch 3: Pérdida = 5.90917931603104 Exactitud = 50.0
Epoch 4: Pérdida = 5.667615422855224 Exactitud = 50.0
Epoch 5: Pérdida = 5.542785493771056 Exactitud = 50.0
Epoch 6: Pérdida = 5.459019076283704 Exactitud = 50.0
Epoch 7: Pérdida = 5.396951534511298 Exactitud = 50.0
Epoch 8: Pérdida = 5.348232950418421 Exactitud = 50.0
Epoch 9: Pérdida = 5.308516558848023 Exactitud = 50.0
Epoch 10: Pérdida = 5.275248903217781 Exactitud = 50.0
Epoch 11: Pérdida = 5.246795974126766 Exactitud = 50.0
Epoch 12: Pérdida = 5.222043454745818 Exactitud = 50.0
Epoch 13: Pérdida = 5.200194131310347 Exactitud = 50.0
Epoch 14: Pérdida = 5.180656764182183 Exactitud = 50.0
Epoch 15: Pérdida = 5.162980880850501 Exactitud = 50.0
Epoch 16: Pérdida = 5.146816062242685 Exactitud = 50.0
Epoch 17: Pérdida = 5.131884956987541 Exactitud = 50.0
Epoch 18: Pérdida = 5

Epoch 322: Pérdida = 0.010954946076123299 Exactitud = 100.0
Epoch 323: Pérdida = 0.01090948739161852 Exactitud = 100.0
Epoch 324: Pérdida = 0.01086442213065313 Exactitud = 100.0
Epoch 325: Pérdida = 0.010819744807403615 Exactitud = 100.0
Epoch 326: Pérdida = 0.01077545004920245 Exactitud = 100.0
Epoch 327: Pérdida = 0.010731532593349089 Exactitud = 100.0
Epoch 328: Pérdida = 0.010687987284035867 Exactitud = 100.0
Epoch 329: Pérdida = 0.010644809069380185 Exactitud = 100.0
Epoch 330: Pérdida = 0.010601992998561014 Exactitud = 100.0
Epoch 331: Pérdida = 0.01055953421905696 Exactitud = 100.0
Epoch 332: Pérdida = 0.010517427973974987 Exactitud = 100.0
Epoch 333: Pérdida = 0.010475669599475297 Exactitud = 100.0
Epoch 334: Pérdida = 0.01043425452228234 Exactitud = 100.0
Epoch 335: Pérdida = 0.010393178257278111 Exactitud = 100.0
Epoch 336: Pérdida = 0.01035243640517931 Exactitud = 100.0
Epoch 337: Pérdida = 0.010312024650290592 Exactitud = 100.0
Epoch 338: Pérdida = 0.010271938758332932 Exac

Epoch 664: Pérdida = 0.004600011654217952 Exactitud = 100.0
Epoch 665: Pérdida = 0.004592466885051044 Exactitud = 100.0
Epoch 666: Pérdida = 0.004584948513131294 Exactitud = 100.0
Epoch 667: Pérdida = 0.0045774564023937266 Exactitud = 100.0
Epoch 668: Pérdida = 0.004569990417693461 Exactitud = 100.0
Epoch 669: Pérdida = 0.004562550424801554 Exactitud = 100.0
Epoch 670: Pérdida = 0.004555136290395176 Exactitud = 100.0
Epoch 671: Pérdida = 0.004547747882050252 Exactitud = 100.0
Epoch 672: Pérdida = 0.004540385068233958 Exactitud = 100.0
Epoch 673: Pérdida = 0.004533047718298695 Exactitud = 100.0
Epoch 674: Pérdida = 0.004525735702471934 Exactitud = 100.0
Epoch 675: Pérdida = 0.004518448891851625 Exactitud = 100.0
Epoch 676: Pérdida = 0.004511187158396815 Exactitud = 100.0
Epoch 677: Pérdida = 0.004503950374921848 Exactitud = 100.0
Epoch 678: Pérdida = 0.004496738415089201 Exactitud = 100.0
Epoch 679: Pérdida = 0.0044895511534012375 Exactitud = 100.0
Epoch 680: Pérdida = 0.004482388465195

Epoch 1006: Pérdida = 0.0029885028167760783 Exactitud = 100.0
Epoch 1007: Pérdida = 0.0029855736233228448 Exactitud = 100.0
Epoch 1008: Pérdida = 0.002982650889263256 Exactitud = 100.0
Epoch 1009: Pérdida = 0.002979734593109039 Exactitud = 100.0
Epoch 1010: Pérdida = 0.0029768247134640312 Exactitud = 100.0
Epoch 1011: Pérdida = 0.0029739212290255143 Exactitud = 100.0
Epoch 1012: Pérdida = 0.002971024118584099 Exactitud = 100.0
Epoch 1013: Pérdida = 0.0029681333610212827 Exactitud = 100.0
Epoch 1014: Pérdida = 0.002965248935311 Exactitud = 100.0
Epoch 1015: Pérdida = 0.002962370820518066 Exactitud = 100.0
Epoch 1016: Pérdida = 0.0029594989957975127 Exactitud = 100.0
Epoch 1017: Pérdida = 0.002956633440395581 Exactitud = 100.0
Epoch 1018: Pérdida = 0.002953774133646723 Exactitud = 100.0
Epoch 1019: Pérdida = 0.0029509210549757137 Exactitud = 100.0
Epoch 1020: Pérdida = 0.002948074183895754 Exactitud = 100.0
Epoch 1021: Pérdida = 0.0029452335000080317 Exactitud = 100.0
Epoch 1022: Pérdida

Epoch 1351: Pérdida = 0.002255145153915748 Exactitud = 100.0
Epoch 1352: Pérdida = 0.002253602039534371 Exactitud = 100.0
Epoch 1353: Pérdida = 0.002252061344429809 Exactitud = 100.0
Epoch 1354: Pérdida = 0.0022505230626997984 Exactitud = 100.0
Epoch 1355: Pérdida = 0.0022489871884611027 Exactitud = 100.0
Epoch 1356: Pérdida = 0.002247453715849292 Exactitud = 100.0
Epoch 1357: Pérdida = 0.0022459226390194108 Exactitud = 100.0
Epoch 1358: Pérdida = 0.002244393952145195 Exactitud = 100.0
Epoch 1359: Pérdida = 0.002242867649418301 Exactitud = 100.0
Epoch 1360: Pérdida = 0.0022413437250498555 Exactitud = 100.0
Epoch 1361: Pérdida = 0.0022398221732700123 Exactitud = 100.0
Epoch 1362: Pérdida = 0.0022383029883266212 Exactitud = 100.0
Epoch 1363: Pérdida = 0.00223678616448667 Exactitud = 100.0
Epoch 1364: Pérdida = 0.0022352716960350617 Exactitud = 100.0
Epoch 1365: Pérdida = 0.0022337595772748383 Exactitud = 100.0
Epoch 1366: Pérdida = 0.0022322498025286242 Exactitud = 100.0
Epoch 1367: Pérd

...

Epoch 28542: Pérdida = 0.0001438083980177406 Exactitud = 100.0
Epoch 28543: Pérdida = 0.0001438035365890806 Exactitud = 100.0
Epoch 28544: Pérdida = 0.0001437986754891814 Exactitud = 100.0
Epoch 28545: Pérdida = 0.00014379381471837612 Exactitud = 100.0
Epoch 28546: Pérdida = 0.00014378895427610963 Exactitud = 100.0
Epoch 28547: Pérdida = 0.00014378409416315906 Exactitud = 100.0
Epoch 28548: Pérdida = 0.00014377923437852523 Exactitud = 100.0
Epoch 28549: Pérdida = 0.00014377437492276324 Exactitud = 100.0
Epoch 28550: Pérdida = 0.00014376951579542896 Exactitud = 100.0
Epoch 28551: Pérdida = 0.00014376465699729964 Exactitud = 100.0
Epoch 28552: Pérdida = 0.00014375979852726496 Exactitud = 100.0
Epoch 28553: Pérdida = 0.00014375494038643518 Exactitud = 100.0
Epoch 28554: Pérdida = 0.000143750082573478 Exactitud = 100.0
Epoch 28555: Pérdida = 0.00014374522508950368 Exactitud = 100.0
Epoch 28556: Pérdida = 0.0001437403679339571 Exactitud = 100.0
Epoch 28557: Pérdida = 0.0001437355111067272 E

Epoch 28879: Pérdida = 0.00014218850869942862 Exactitud = 100.0
Epoch 28880: Pérdida = 0.0001421837562464435 Exactitud = 100.0
Epoch 28881: Pérdida = 0.00014217900411144898 Exactitud = 100.0
Epoch 28882: Pérdida = 0.00014217425229433404 Exactitud = 100.0
Epoch 28883: Pérdida = 0.0001421695007950987 Exactitud = 100.0
Epoch 28884: Pérdida = 0.0001421647496135209 Exactitud = 100.0
Epoch 28885: Pérdida = 0.00014215999874971167 Exactitud = 100.0
Epoch 28886: Pérdida = 0.00014215524820367098 Exactitud = 100.0
Epoch 28887: Pérdida = 0.00014215049797539886 Exactitud = 100.0
Epoch 28888: Pérdida = 0.0001421457480645622 Exactitud = 100.0
Epoch 28889: Pérdida = 0.0001421409984716051 Exactitud = 100.0
Epoch 28890: Pérdida = 0.00014213624919608348 Exactitud = 100.0
Epoch 28891: Pérdida = 0.00014213150023833043 Exactitud = 100.0
Epoch 28892: Pérdida = 0.00014212675159801282 Exactitud = 100.0
Epoch 28893: Pérdida = 0.0001421220032752417 Exactitud = 100.0
Epoch 28894: Pérdida = 0.000142117255269684 Ex

Epoch 29219: Pérdida = 0.00014059078964409437 Exactitud = 100.0
Epoch 29220: Pérdida = 0.000140586143460446 Exactitud = 100.0
Epoch 29221: Pérdida = 0.00014058149758435117 Exactitud = 100.0
Epoch 29222: Pérdida = 0.00014057685201525474 Exactitud = 100.0
Epoch 29223: Pérdida = 0.00014057220675337874 Exactitud = 100.0
Epoch 29224: Pérdida = 0.00014056756179883415 Exactitud = 100.0
Epoch 29225: Pérdida = 0.00014056291715139904 Exactitud = 100.0
Epoch 29226: Pérdida = 0.0001405582728109623 Exactitud = 100.0
Epoch 29227: Pérdida = 0.00014055362877741286 Exactitud = 100.0
Epoch 29228: Pérdida = 0.00014054898505130598 Exactitud = 100.0
Epoch 29229: Pérdida = 0.00014054434163219743 Exactitud = 100.0
Epoch 29230: Pérdida = 0.0001405396985201983 Exactitud = 100.0
Epoch 29231: Pérdida = 0.00014053505571486445 Exactitud = 100.0
Epoch 29232: Pérdida = 0.0001405304132163069 Exactitud = 100.0
Epoch 29233: Pérdida = 0.0001405257710248588 Exactitud = 100.0
Epoch 29234: Pérdida = 0.0001405211291406311 E

Epoch 29553: Pérdida = 0.00013905586629619238 Exactitud = 100.0
Epoch 29554: Pérdida = 0.00013905132106922837 Exactitud = 100.0
Epoch 29555: Pérdida = 0.00013904677613915878 Exactitud = 100.0
Epoch 29556: Pérdida = 0.00013904223150664976 Exactitud = 100.0
Epoch 29557: Pérdida = 0.0001390376871713683 Exactitud = 100.0
Epoch 29558: Pérdida = 0.0001390331431334253 Exactitud = 100.0
Epoch 29559: Pérdida = 0.00013902859939226566 Exactitud = 100.0
Epoch 29560: Pérdida = 0.00013902405594844462 Exactitud = 100.0
Epoch 29561: Pérdida = 0.000139019512801851 Exactitud = 100.0
Epoch 29562: Pérdida = 0.00013901496995226287 Exactitud = 100.0
Epoch 29563: Pérdida = 0.00013901042739968017 Exactitud = 100.0
Epoch 29564: Pérdida = 0.00013900588514410289 Exactitud = 100.0
Epoch 29565: Pérdida = 0.00013900134318597514 Exactitud = 100.0
Epoch 29566: Pérdida = 0.0001389968015242977 Exactitud = 100.0
Epoch 29567: Pérdida = 0.0001389922601597367 Exactitud = 100.0
Epoch 29568: Pérdida = 0.00013898771909229217 

Epoch 29891: Pérdida = 0.00013753632735240856 Exactitud = 100.0
Epoch 29892: Pérdida = 0.00013753188097325822 Exactitud = 100.0
Epoch 29893: Pérdida = 0.0001375274348818976 Exactitud = 100.0
Epoch 29894: Pérdida = 0.00013752298907821568 Exactitud = 100.0
Epoch 29895: Pérdida = 0.00013751854356176834 Exactitud = 100.0
Epoch 29896: Pérdida = 0.00013751409833277761 Exactitud = 100.0
Epoch 29897: Pérdida = 0.0001375096533915766 Exactitud = 100.0
Epoch 29898: Pérdida = 0.00013750520873816532 Exactitud = 100.0
Epoch 29899: Pérdida = 0.00013750076437187757 Exactitud = 100.0
Epoch 29900: Pérdida = 0.00013749632029315747 Exactitud = 100.0
Epoch 29901: Pérdida = 0.000137491876501672 Exactitud = 100.0
Epoch 29902: Pérdida = 0.00013748743299753208 Exactitud = 100.0
Epoch 29903: Pérdida = 0.00013748298978073775 Exactitud = 100.0
Epoch 29904: Pérdida = 0.00013747854685173315 Exactitud = 100.0
Epoch 29905: Pérdida = 0.00013747410420974105 Exactitud = 100.0
Epoch 29906: Pérdida = 0.0001374696618548724

#### Convergencia rápida con activación relu

In [38]:
#Preparamos la información, y las etiquetas
X = np.array([[0, 0], [0, 1], [1, 0], [1, 1]])
y = np.array([[1, 0, 0, 1]]).T
np.random.seed(0)
# Tasa de aprendizaje, dimensiones internas y variación de pesos efectivos para función de activación sigmoide
W1, W2, perdidas, exactitudes = retroprop(X, y, alpha = 0.001, n_epocas = 300, dim_ocultas = [10,10], varianza_pesos = 2, actv_int = 'relu')

Epoch 0: Pérdida = 13.29369673755029 Exactitud = 50.0
Epoch 1: Pérdida = 1.6429945624209608 Exactitud = 50.0
Epoch 2: Pérdida = 1.0852294490881285 Exactitud = 75.0
Epoch 3: Pérdida = 1.036056185102677 Exactitud = 75.0
Epoch 4: Pérdida = 1.0030451209444566 Exactitud = 75.0
Epoch 5: Pérdida = 0.9788044071752234 Exactitud = 75.0
Epoch 6: Pérdida = 0.9601030853943606 Exactitud = 100.0
Epoch 7: Pérdida = 0.9452134167403429 Exactitud = 100.0
Epoch 8: Pérdida = 0.9330972403196452 Exactitud = 100.0
Epoch 9: Pérdida = 0.923080091522141 Exactitud = 100.0
Epoch 10: Pérdida = 0.9146981945884607 Exactitud = 100.0
Epoch 11: Pérdida = 0.9076184771259647 Exactitud = 100.0
Epoch 12: Pérdida = 0.9015933526977296 Exactitud = 100.0
Epoch 13: Pérdida = 0.8964335774279566 Exactitud = 100.0
Epoch 14: Pérdida = 0.8919911584259599 Exactitud = 100.0
Epoch 15: Pérdida = 0.8881481603094842 Exactitud = 100.0
Epoch 16: Pérdida = 0.8848091268578056 Exactitud = 100.0
Epoch 17: Pérdida = 0.8818958002524551 Exactitud =

Epoch 197: Pérdida = 0.7942767771412464 Exactitud = 100.0
Epoch 198: Pérdida = 0.7939743180115515 Exactitud = 100.0
Epoch 199: Pérdida = 0.7936725058486767 Exactitud = 100.0
Epoch 200: Pérdida = 0.7933713341324335 Exactitud = 100.0
Epoch 201: Pérdida = 0.7930707964359457 Exactitud = 100.0
Epoch 202: Pérdida = 0.792770886424065 Exactitud = 100.0
Epoch 203: Pérdida = 0.7924715978518633 Exactitud = 100.0
Epoch 204: Pérdida = 0.7921729245630984 Exactitud = 100.0
Epoch 205: Pérdida = 0.791874860488753 Exactitud = 100.0
Epoch 206: Pérdida = 0.7915773996455716 Exactitud = 100.0
Epoch 207: Pérdida = 0.7912805361346366 Exactitud = 100.0
Epoch 208: Pérdida = 0.7909842641399675 Exactitud = 100.0
Epoch 209: Pérdida = 0.7906885779271443 Exactitud = 100.0
Epoch 210: Pérdida = 0.790393471841963 Exactitud = 100.0
Epoch 211: Pérdida = 0.7900989403091014 Exactitud = 100.0
Epoch 212: Pérdida = 0.789804977830829 Exactitud = 100.0
Epoch 213: Pérdida = 0.7895115789857201 Exactitud = 100.0
Epoch 214: Pérdida

Epoch 405: Pérdida = 0.7398001799478814 Exactitud = 100.0
Epoch 406: Pérdida = 0.7395641554875017 Exactitud = 100.0
Epoch 407: Pérdida = 0.7393282991236845 Exactitud = 100.0
Epoch 408: Pérdida = 0.7390926102526484 Exactitud = 100.0
Epoch 409: Pérdida = 0.7388570882761504 Exactitud = 100.0
Epoch 410: Pérdida = 0.7386217326014294 Exactitud = 100.0
Epoch 411: Pérdida = 0.7383865426411449 Exactitud = 100.0
Epoch 412: Pérdida = 0.7381515178133184 Exactitud = 100.0
Epoch 413: Pérdida = 0.7379166575412741 Exactitud = 100.0
Epoch 414: Pérdida = 0.7376819612535822 Exactitud = 100.0
Epoch 415: Pérdida = 0.7374474283840019 Exactitud = 100.0
Epoch 416: Pérdida = 0.7372130583714236 Exactitud = 100.0
Epoch 417: Pérdida = 0.736978850659812 Exactitud = 100.0
Epoch 418: Pérdida = 0.7367448046981568 Exactitud = 100.0
Epoch 419: Pérdida = 0.7365109199404108 Exactitud = 100.0
Epoch 420: Pérdida = 0.7362771958454448 Exactitud = 100.0
Epoch 421: Pérdida = 0.7360436318769856 Exactitud = 100.0
Epoch 422: Pérd

Epoch 618: Pérdida = 0.692677902074378 Exactitud = 100.0
Epoch 619: Pérdida = 0.6924695412594302 Exactitud = 100.0
Epoch 620: Pérdida = 0.6922612877045579 Exactitud = 100.0
Epoch 621: Pérdida = 0.6920531412867195 Exactitud = 100.0
Epoch 622: Pérdida = 0.6918451018835607 Exactitud = 100.0
Epoch 623: Pérdida = 0.6916371693734049 Exactitud = 100.0
Epoch 624: Pérdida = 0.6914293436352548 Exactitud = 100.0
Epoch 625: Pérdida = 0.6912216245487803 Exactitud = 100.0
Epoch 626: Pérdida = 0.6910140119943129 Exactitud = 100.0
Epoch 627: Pérdida = 0.6908065058528414 Exactitud = 100.0
Epoch 628: Pérdida = 0.6905991060060072 Exactitud = 100.0
Epoch 629: Pérdida = 0.6903918123360969 Exactitud = 100.0
Epoch 630: Pérdida = 0.6901846247260359 Exactitud = 100.0
Epoch 631: Pérdida = 0.6899775430593822 Exactitud = 100.0
Epoch 632: Pérdida = 0.6897705672203281 Exactitud = 100.0
Epoch 633: Pérdida = 0.6895636970936806 Exactitud = 100.0
Epoch 634: Pérdida = 0.6893569325648703 Exactitud = 100.0
Epoch 635: Pérd

Epoch 832: Pérdida = 0.6503771554012574 Exactitud = 100.0
Epoch 833: Pérdida = 0.650189683008944 Exactitud = 100.0
Epoch 834: Pérdida = 0.6500023007731025 Exactitud = 100.0
Epoch 835: Pérdida = 0.6498150086379175 Exactitud = 100.0
Epoch 836: Pérdida = 0.6496278065476833 Exactitud = 100.0
Epoch 837: Pérdida = 0.6494406944468087 Exactitud = 100.0
Epoch 838: Pérdida = 0.6492536722798176 Exactitud = 100.0
Epoch 839: Pérdida = 0.649066739991336 Exactitud = 100.0
Epoch 840: Pérdida = 0.6488798975261069 Exactitud = 100.0
Epoch 841: Pérdida = 0.6486931448289797 Exactitud = 100.0
Epoch 842: Pérdida = 0.6485064818449109 Exactitud = 100.0
Epoch 843: Pérdida = 0.6483199085189646 Exactitud = 100.0
Epoch 844: Pérdida = 0.6481334247963101 Exactitud = 100.0
Epoch 845: Pérdida = 0.6479470306222251 Exactitud = 100.0
Epoch 846: Pérdida = 0.647760725942088 Exactitud = 100.0
Epoch 847: Pérdida = 0.647574510701385 Exactitud = 100.0
Epoch 848: Pérdida = 0.6473883848457012 Exactitud = 100.0
Epoch 849: Pérdida

...

Epoch 29143: Pérdida = 2.778994698168681 Exactitud = 50.0
Epoch 29144: Pérdida = 2.778994505979637 Exactitud = 50.0
Epoch 29145: Pérdida = 2.778994313788738 Exactitud = 50.0
Epoch 29146: Pérdida = 2.778994121595986 Exactitud = 50.0
Epoch 29147: Pérdida = 2.77899392940138 Exactitud = 50.0
Epoch 29148: Pérdida = 2.7789937372049205 Exactitud = 50.0
Epoch 29149: Pérdida = 2.778993545006607 Exactitud = 50.0
Epoch 29150: Pérdida = 2.7789933528064386 Exactitud = 50.0
Epoch 29151: Pérdida = 2.7789931606044167 Exactitud = 50.0
Epoch 29152: Pérdida = 2.7789929684005408 Exactitud = 50.0
Epoch 29153: Pérdida = 2.7789927761948103 Exactitud = 50.0
Epoch 29154: Pérdida = 2.778992583987226 Exactitud = 50.0
Epoch 29155: Pérdida = 2.778992391777787 Exactitud = 50.0
Epoch 29156: Pérdida = 2.7789921995664937 Exactitud = 50.0
Epoch 29157: Pérdida = 2.7789920073533465 Exactitud = 50.0
Epoch 29158: Pérdida = 2.778991815138345 Exactitud = 50.0
Epoch 29159: Pérdida = 2.778991622921489 Exactitud = 50.0
Epoch 29

Epoch 29341: Pérdida = 2.778956608526471 Exactitud = 50.0
Epoch 29342: Pérdida = 2.778956415969506 Exactitud = 50.0
Epoch 29343: Pérdida = 2.7789562234106784 Exactitud = 50.0
Epoch 29344: Pérdida = 2.778956030849988 Exactitud = 50.0
Epoch 29345: Pérdida = 2.778955838287435 Exactitud = 50.0
Epoch 29346: Pérdida = 2.77895564572302 Exactitud = 50.0
Epoch 29347: Pérdida = 2.7789554531567404 Exactitud = 50.0
Epoch 29348: Pérdida = 2.7789552605885994 Exactitud = 50.0
Epoch 29349: Pérdida = 2.7789550680185955 Exactitud = 50.0
Epoch 29350: Pérdida = 2.7789548754467277 Exactitud = 50.0
Epoch 29351: Pérdida = 2.778954682872998 Exactitud = 50.0
Epoch 29352: Pérdida = 2.7789544902974055 Exactitud = 50.0
Epoch 29353: Pérdida = 2.7789542977199484 Exactitud = 50.0
Epoch 29354: Pérdida = 2.77895410514063 Exactitud = 50.0
Epoch 29355: Pérdida = 2.778953912559447 Exactitud = 50.0
Epoch 29356: Pérdida = 2.778953719976401 Exactitud = 50.0
Epoch 29357: Pérdida = 2.7789535273914927 Exactitud = 50.0
Epoch 29

Epoch 29534: Pérdida = 2.7789194104689474 Exactitud = 50.0
Epoch 29535: Pérdida = 2.778919217551669 Exactitud = 50.0
Epoch 29536: Pérdida = 2.778919024632519 Exactitud = 50.0
Epoch 29537: Pérdida = 2.778918831711497 Exactitud = 50.0
Epoch 29538: Pérdida = 2.7789186387886042 Exactitud = 50.0
Epoch 29539: Pérdida = 2.77891844586384 Exactitud = 50.0
Epoch 29540: Pérdida = 2.7789182529372045 Exactitud = 50.0
Epoch 29541: Pérdida = 2.7789180600086976 Exactitud = 50.0
Epoch 29542: Pérdida = 2.7789178670783192 Exactitud = 50.0
Epoch 29543: Pérdida = 2.7789176741460686 Exactitud = 50.0
Epoch 29544: Pérdida = 2.7789174812119475 Exactitud = 50.0
Epoch 29545: Pérdida = 2.778917288275953 Exactitud = 50.0
Epoch 29546: Pérdida = 2.7789170953380884 Exactitud = 50.0
Epoch 29547: Pérdida = 2.7789169023983513 Exactitud = 50.0
Epoch 29548: Pérdida = 2.778916709456743 Exactitud = 50.0
Epoch 29549: Pérdida = 2.778916516513262 Exactitud = 50.0
Epoch 29550: Pérdida = 2.77891632356791 Exactitud = 50.0
Epoch 2

Epoch 29728: Pérdida = 2.778881949430939 Exactitud = 50.0
Epoch 29729: Pérdida = 2.7788817561497905 Exactitud = 50.0
Epoch 29730: Pérdida = 2.7788815628667622 Exactitud = 50.0
Epoch 29731: Pérdida = 2.7788813695818537 Exactitud = 50.0
Epoch 29732: Pérdida = 2.7788811762950654 Exactitud = 50.0
Epoch 29733: Pérdida = 2.7788809830063967 Exactitud = 50.0
Epoch 29734: Pérdida = 2.7788807897158483 Exactitud = 50.0
Epoch 29735: Pérdida = 2.778880596423419 Exactitud = 50.0
Epoch 29736: Pérdida = 2.7788804031291097 Exactitud = 50.0
Epoch 29737: Pérdida = 2.77888020983292 Exactitud = 50.0
Epoch 29738: Pérdida = 2.77888001653485 Exactitud = 50.0
Epoch 29739: Pérdida = 2.7788798232348992 Exactitud = 50.0
Epoch 29740: Pérdida = 2.7788796299330687 Exactitud = 50.0
Epoch 29741: Pérdida = 2.778879436629357 Exactitud = 50.0
Epoch 29742: Pérdida = 2.7788792433237646 Exactitud = 50.0
Epoch 29743: Pérdida = 2.7788790500162923 Exactitud = 50.0
Epoch 29744: Pérdida = 2.7788788567069393 Exactitud = 50.0
Epoc

Epoch 29927: Pérdida = 2.778843449385319 Exactitud = 50.0
Epoch 29928: Pérdida = 2.7788432557291505 Exactitud = 50.0
Epoch 29929: Pérdida = 2.7788430620710924 Exactitud = 50.0
Epoch 29930: Pérdida = 2.778842868411146 Exactitud = 50.0
Epoch 29931: Pérdida = 2.77884267474931 Exactitud = 50.0
Epoch 29932: Pérdida = 2.778842481085585 Exactitud = 50.0
Epoch 29933: Pérdida = 2.7788422874199705 Exactitud = 50.0
Epoch 29934: Pérdida = 2.778842093752467 Exactitud = 50.0
Epoch 29935: Pérdida = 2.7788419000830737 Exactitud = 50.0
Epoch 29936: Pérdida = 2.7788417064117916 Exactitud = 50.0
Epoch 29937: Pérdida = 2.7788415127386195 Exactitud = 50.0
Epoch 29938: Pérdida = 2.7788413190635577 Exactitud = 50.0
Epoch 29939: Pérdida = 2.7788411253866068 Exactitud = 50.0
Epoch 29940: Pérdida = 2.7788409317077662 Exactitud = 50.0
Epoch 29941: Pérdida = 2.778840738027036 Exactitud = 50.0
Epoch 29942: Pérdida = 2.7788405443444164 Exactitud = 50.0
Epoch 29943: Pérdida = 2.778840350659907 Exactitud = 50.0
Epoch

### Ejercicio 3 - Regresión Lineal con PyTorch

**La resolución de este ejercicio se encuentra en el notebook titulado [1e_regresion_lineal_tarea.ipynb](https://github.com/Mariuki/CursoAprendizajeProfundoIIMAS/blob/master/notebooks/1e_regresion_lineal_tarea.ipynb)**


### Ejercicio 4 - Red completamente conectada con PyTorch

**La resolución de este ejercicio se encuentra en el notebook titulado [1g_mlp_tarea.ipynb](https://github.com/Mariuki/CursoAprendizajeProfundoIIMAS/blob/master/notebooks/1g_mlp_tarea.ipynb)**